이미지 크기 확인

In [26]:
import cv2

# 이미지 파일 경로 설정
image_file = '/media/ssd3/lab/sypark/KITTI/object/2d_object/data_object_image_2/testing/image_2/000100.png'

# 이미지 읽기
img = cv2.imread(image_file)

# 이미지 크기 확인
img_h, img_w = img.shape[:2]

# 출력
print(f"Image width: {img_w}, Image height: {img_h}")

Image width: 1242, Image height: 375


### 1. 필요한 라이브러리 및 기본 설정

In [5]:
import os
import numpy as np
import cv2
from multiprocessing import Pool ###변환속도가 너무 느릴시 멀티프로세싱 사용


# 경로 설정
base_path = '/media/ssd3/lab/sypark/KITTI/object/2d_object/data_object_image_2/training/image_2'
# velo_base_path = '/media/ssd3/lab/sypark/KITTI/object/2d_object/data_object_velodyne/testing/velodyne' ### 원본데이터
velo_base_path = '/media/ssd3/lab/jojeon/KITTI/data_spoofing/velodyne/train_add' ###spoofing된 파일 상대로 수정
calib_base_path = '/media/ssd3/lab/sypark/KITTI/object/2d_object/data_object_calib/training/calib'
output_base_path = '/media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add' ## spoofing - delete
# output_base_path = '/media/ssd3/lab/jojeon/KITTI/data_object/test/rgb_depth_intensity' ##원본


# 출력 디렉토리 생성
if not os.path.exists(output_base_path):
    os.makedirs(output_base_path)

# 이미지 파일 리스트
image_files = sorted(os.listdir(base_path))


### 2. 캘리브레이션 파일 및 LiDAR 데이터 로드 함수

In [6]:
def load_calibration(calib_file):
    """
    캘리브레이션 파일에서 필요한 행렬을 로드합니다.
    """
    with open(calib_file, 'r') as f:
        lines = f.readlines()
        
    P2 = np.array(list(map(float, lines[2].split()[1:]))).reshape(3, 4)
    R0_rect = np.array(list(map(float, lines[4].split()[1:]))).reshape(3, 3)
    Tr_velo_to_cam = np.array(list(map(float, lines[5].split()[1:]))).reshape(3, 4)
    
    # 행렬 확장
    Tr_velo_to_cam = np.vstack((Tr_velo_to_cam, [0, 0, 0, 1]))
    R0_rect_4x4 = np.eye(4)
    R0_rect_4x4[:3, :3] = R0_rect
    
    return P2, R0_rect_4x4, Tr_velo_to_cam

def load_lidar_data(velo_path):
    """
    LiDAR 데이터(.bin 파일)를 로드합니다.
    """
    lidar_data = np.fromfile(velo_path, dtype=np.float32).reshape(-1, 4)
    xyz = lidar_data[:, :3]  # x, y, z 좌표
    intensity = lidar_data[:, 3]  # intensity 값
    return xyz, intensity


### 3. 깊이값 계산 및 이미지 매핑
카메라 좌표계 기준 z축 - 깊이값계산

In [7]:
def map_lidar_to_image(xyz, intensity, P2, R0_rect_4x4, Tr_velo_to_cam, img_shape):
    """
    LiDAR 포인트를 이미지 평면에 매핑하고, 깊이값을 카메라 좌표계의 Z 축 값(s)으로 계산합니다.
    후방 데이터는 필터링하여 제외합니다. 
    제외 안할시 -> r,g,b 값과 다시 매칭할때 카메라 뒷편의 라이다 값도 매칭되어 나옴.
    """
    # 1. 동차 좌표로 변환 (LiDAR 포인트를 동차 좌표로 변경)
    XYZ1 = np.hstack((xyz, np.ones((xyz.shape[0], 1))))  # LiDAR (X, Y, Z, 1)로 확장
    xy1 = P2 @ R0_rect_4x4 @ Tr_velo_to_cam @ XYZ1.T  # 카메라 좌표계로 변환

    # 2. 깊이값 계산 (카메라 좌표계의 Z 축 값)
    s = xy1[2, :]  # Z 축 값 (카메라 좌표계의 깊이값)

    # 3. 후방 데이터 필터링 (Z 축 값이 0 이하인 포인트 제거)
    valid_indices = s > 0  # Z 값이 양수인 데이터만 선택 (카메라 앞쪽에 있는 데이터만 사용)
    XYZ1 = XYZ1[valid_indices]  # 유효한 XYZ1 좌표
    xy1 = xy1[:, valid_indices]  # 유효한 투영 결과
    s = s[valid_indices]  # 유효한 깊이값 (Z 축 값)

    # 4. 2D 이미지 평면 좌표 계산 (투영된 이미지 상의 X, Y 좌표)
    x = (xy1[0, :] / s).astype(int)  # X 좌표 (정수로 변환)
    y = (xy1[1, :] / s).astype(int)  # Y 좌표 (정수로 변환)

    # 5. 이미지 크기에 맞는 4채널 이미지 생성 (H, W, 4)
    height, width = img_shape[:2]  # 이미지 크기 가져오기 (높이, 너비)
    image_4channel = np.zeros((height, width, 4), dtype=np.float32)  # 4채널 이미지 초기화
    image_4channel[:, :, 3] = -1  # 깊이값 초기화 (-1은 유효하지 않은 영역)

    # 6. 유효한 좌표 필터링 (이미지 경계 내에 있는 포인트만 사용)
    valid_image_indices = (x >= 0) & (x < width) & (y >= 0) & (y < height)  # 이미지 경계 내 포인트
    x = x[valid_image_indices]
    y = y[valid_image_indices]
    s = s[valid_image_indices]  # Z 축 값 (깊이값)도 필터링

    # 7. 깊이값 할당 (Z 축 값 기반 깊이값을 이미지에 저장)
    for i in range(len(x)):
        image_4channel[y[i], x[i], 3] = s[i]  # 카메라 좌표계의 Z 축 값 저장

    return image_4channel, x, y  # 투영된 이미지 좌표(x, y)와 4채널 이미지를 반환



### 4. 데이터 처리 및 저장

In [4]:
def process_file(image_file):
    """
    주어진 이미지 파일에 대해 원본 velodyne 데이터를 처리합니다.
    """

    # 파일 ID 추출 및 경로 설정
    file_id = image_file.split('.')[0]  # 예: 000002
    image_path = os.path.join(base_path, image_file)  # 이미지 파일 경로
    velo_path = os.path.join(velo_base_path, f"{file_id}.bin")  # 원본 LiDAR 파일 경로
    calib_path = os.path.join(calib_base_path, f"{file_id}.txt")  # 캘리브레이션 파일 경로
    output_txt_path = os.path.join(output_base_path, f"{file_id}.txt")  # 결과 저장 경로

    # 이미 처리된 파일 건너뛰기
    if os.path.exists(output_txt_path):
        print(f"File already exists: {output_txt_path}, skipping.")
        return

    # 파일 존재 여부 확인
    if not os.path.exists(velo_path) or not os.path.exists(calib_path):
        print(f"Missing file(s) for {file_id}, skipping.")
        return

    # 이미지 및 캘리브레이션 로드
    img = cv2.imread(image_path)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)  # BGR → RGB 변환
    P2, R0_rect_4x4, Tr_velo_to_cam = load_calibration(calib_path)

    # LiDAR 데이터 로드
    xyz, intensity = load_lidar_data(velo_path)

    # LiDAR 데이터를 이미지로 매핑
    image_4channel, x, y = map_lidar_to_image(xyz, intensity, P2, R0_rect_4x4, Tr_velo_to_cam, img.shape)

    # 이미지와 매핑된 데이터의 크기를 맞추기
    min_height = min(img.shape[0], image_4channel.shape[0])  # 이미지 높이 조정
    min_width = min(img.shape[1], image_4channel.shape[1])  # 이미지 너비 조정
    img = img[:min_height, :min_width, :]  # 이미지 크기 조정
    image_4channel = image_4channel[:min_height, :min_width, :]  # 매핑된 데이터 크기 조정

    # 텍스트 파일 저장
    with open(output_txt_path, 'w') as f:
        f.write(f"# Image: {image_file}\n")
        f.write(f"# Image Path: {image_path}\n")
        f.write(f"# LiDAR Path: {velo_path}\n")
        f.write(f"# Calibration Path: {calib_path}\n")
        f.write(f"# Image Size: {min_width}x{min_height}\n")
        f.write(f"# Format: R G B Depth Intensity\n")
        f.write("#\n")

        # RGB와 Depth, Intensity 값을 텍스트로 저장
        for i in range(min_height):
            for j in range(min_width):
                r, g, b = img[i, j, :]  # RGB 값
                d = image_4channel[i, j, 3]  # 깊이값
                intensity_value = -1  # 기본값
                idx = np.where((x == j) & (y == i))[0]  # 매핑된 좌표 찾기
                if len(idx) > 0:
                    intensity_value = intensity[idx[0]]  # Intensity 값
                f.write(f"{int(r)} {int(g)} {int(b)} {d:.6f} {intensity_value:.6f}\n")

    print(f"Saved: {output_txt_path}")  # 저장된 파일 경로 출력



### 4-1. spoofing된 파일 rgb+d+i 데이터 처리 및 저장

In [8]:
def process_file(image_file):
    """
    주어진 이미지 파일에 대해 spoofing된 velodyne 데이터를 처리합니다.
    """
    # 파일 ID 추출 및 관련 경로 설정
    file_id = image_file.split('.')[0]
    velo_dir = os.path.join(velo_base_path, file_id)
    output_dir = os.path.join(output_base_path, file_id)

    # spoofing된 velodyne 데이터가 없으면 스킵
    if not os.path.exists(velo_dir):
        print(f"Spoofed velodyne directory not found for {file_id}, skipping.")
        return

    # 출력 디렉토리 생성
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    # spoofing된 .bin 파일 리스트 가져오기
    bin_files = sorted(os.listdir(velo_dir))
    image_path = os.path.join(base_path, image_file)
    calib_path = os.path.join(calib_base_path, f"{file_id}.txt")

    # 이미지 및 캘리브레이션 파일 확인
    if not os.path.exists(image_path) or not os.path.exists(calib_path):
        print(f"Missing image or calibration file for {file_id}, skipping.")
        return

    # 이미지 및 캘리브레이션 로드
    img = cv2.imread(image_path)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)  # BGR → RGB 변환
    P2, R0_rect_4x4, Tr_velo_to_cam = load_calibration(calib_path)

    # spoofing된 .bin 파일 처리
    for bin_file in bin_files:
        velo_path = os.path.join(velo_dir, bin_file) # 예: 000002/000002-1.bin
        xyz, intensity = load_lidar_data(velo_path)

        # LiDAR 데이터를 이미지로 매핑
        image_4channel, x, y = map_lidar_to_image(xyz, intensity, P2, R0_rect_4x4, Tr_velo_to_cam, img.shape)

        # 이미지와 매핑된 데이터 image_4channel의 크기 조정
        min_height = min(img.shape[0], image_4channel.shape[0])
        min_width = min(img.shape[1], image_4channel.shape[1])

        img = img[:min_height, :min_width, :]
        image_4channel = image_4channel[:min_height, :min_width, :]

        # 텍스트 파일 저장 경로 설정
        output_txt_path = os.path.join(output_dir, bin_file.replace('.bin', '.txt'))

        # 텍스트 파일 저장
        with open(output_txt_path, 'w') as f:
            f.write(f"# Image: {image_file}\n")
            f.write(f"# Image Path: {image_path}\n")
            f.write(f"# LiDAR Path: {velo_path}\n")
            f.write(f"# Calibration Path: {calib_path}\n")
            f.write(f"# Image Size: {min_width}x{min_height}\n")
            f.write(f"# Format: R G B Depth Intensity\n")
            f.write("#\n")

            for i in range(min_height):
                for j in range(min_width):
                    r, g, b = img[i, j, :]  # 이미지 RGB 값
                    d = image_4channel[i, j, 3]  # 깊이값
                    intensity_value = -1
                    idx = np.where((x == j) & (y == i))[0]
                    if len(idx) > 0:
                        intensity_value = intensity[idx[0]]
                    f.write(f"{int(r)} {int(g)} {int(b)} {d:.6f} {intensity_value:.6f}\n")

        print(f"Saved: {output_txt_path}")



### 5. 멀티프로세싱 실행시 돌리면됨
process_file 함수를 병렬로 실행합니다.( 속도가 너무 느려서 멀티프로세싱하도록 넣어놨음)

In [9]:
if __name__ == "__main__":
    from multiprocessing import Pool

    # 멀티프로세싱 실행
    with Pool(processes=100) as pool:  # 사용할 프로세스 수 지정 (n개)
        pool.map(process_file, image_files)  # image_files 리스트 병렬 처리


Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000228/000228-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000874/000874-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000285/000285-1.txtSaved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000703/000703-1.txt

Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000931/000931-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/001406/001406-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000247/000247-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000741/000741-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000760/000760-1.txt
Saved: /media/ssd3/lab/jojeon/KITTI/data_object/training/rgb_depth_intensity_add/000038/000

_____________________________________________________________________________________________________-